# Inspection of files


In [1]:
import fsspec
import xarray as xr
import hvplot.xarray

In [2]:
fs = fsspec.filesystem('s3', anon=True)

In [3]:
flist = fs.ls('s3://noaa-nwm-retrospective-2-1-pds/')
flist

['noaa-nwm-retrospective-2-1-pds/forcing',
 'noaa-nwm-retrospective-2-1-pds/index.html',
 'noaa-nwm-retrospective-2-1-pds/model_output']

In [4]:
flist = fs.glob('noaa-nwm-retrospective-2-1-pds/model_output/*')
print(flist[0])
print(flist[-1])

noaa-nwm-retrospective-2-1-pds/model_output/1979
noaa-nwm-retrospective-2-1-pds/model_output/2020


In [5]:
flist = fs.glob('noaa-nwm-retrospective-2-1-pds/model_output/1980/*LDAS*')
flist[:5]

['noaa-nwm-retrospective-2-1-pds/model_output/1980/198001010000.LDASOUT_DOMAIN1.comp',
 'noaa-nwm-retrospective-2-1-pds/model_output/1980/198001010300.LDASOUT_DOMAIN1.comp',
 'noaa-nwm-retrospective-2-1-pds/model_output/1980/198001010600.LDASOUT_DOMAIN1.comp',
 'noaa-nwm-retrospective-2-1-pds/model_output/1980/198001010900.LDASOUT_DOMAIN1.comp',
 'noaa-nwm-retrospective-2-1-pds/model_output/1980/198001011200.LDASOUT_DOMAIN1.comp']

Okay, so at this point we've learned that we have 3-hourly output over roughly 40 years

In [6]:
# %%time
# flist = fs.glob('noaa-nwm-retrospective-2-1-pds/model_output/*/*LDAS*')   # this is slow
40 * 365 * 24 / 3

116800.0

So about 117,000 files! 

In [7]:
ds = xr.open_dataset(fs.open(flist[0]), chunks={})

In [18]:
ds.data_vars

Data variables:
    crs       |S1 ...
    COSZ      (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    FSA       (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    FIRA      (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    HFX       (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    LH        (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    EDIR      (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    ALBEDO    (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    UGDRNOFF  (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    TRAD      (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    SOIL_W    (time, y, soil_layers_stag, x) float64 dask.array<chunksize=(1, 3840, 4, 4608), meta=np.ndarray>
    SOIL_M    (time, y, soil_layers_stag,

In [19]:
ds = ds[['ACCET', 'SNEQV', 'FSNO']]

In [20]:
ds

<xarray.Dataset>
Dimensions:  (time: 1, y: 3840, x: 4608)
Coordinates:
  * time     (time) datetime64[ns] 1980-01-01
  * x        (x) float64 -2.303e+06 -2.302e+06 ... 2.303e+06 2.304e+06
  * y        (y) float64 -1.92e+06 -1.919e+06 -1.918e+06 ... 1.918e+06 1.919e+06
Data variables:
    ACCET    (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    SNEQV    (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
    FSNO     (time, y, x) float64 dask.array<chunksize=(1, 3840, 4608), meta=np.ndarray>
Attributes:
    TITLE:                      OUTPUT FROM WRF-Hydro v5.2.0-beta2
    model_initialization_time:  1979-10-01_00:00:00
    model_output_valid_time:    1980-01-01_00:00:00
    model_total_valid_times:    736
    Conventions:                CF-1.6
    code_version:               v5.2.0-beta2
    model_output_type:          land
    model_configuration:        retrospective
    proj4:                      +proj=lcc +units=m +a=6370000.0 +b=6370000.0 ...
    GDAL_DataType:              Generic

In [21]:
ds.ACCET

<xarray.DataArray 'ACCET' (time: 1, y: 3840, x: 4608)>
dask.array<open_dataset-e0774b187f821db7bc13d11268d75af0ACCET, shape=(1, 3840, 4608), dtype=float64, chunksize=(1, 3840, 4608), chunktype=numpy.ndarray>
Coordinates:
  * time     (time) datetime64[ns] 1980-01-01
  * x        (x) float64 -2.303e+06 -2.302e+06 ... 2.303e+06 2.304e+06
  * y        (y) float64 -1.92e+06 -1.919e+06 -1.918e+06 ... 1.918e+06 1.919e+06
Attributes:
    long_name:       Accumulated total ET
    units:           mm
    grid_mapping:    crs
    valid_range:     [  -100000 100000000]
    esri_pe_string:  PROJCS["Lambert_Conformal_Conic",GEOGCS["GCS_Sphere",DAT...

The data is chunked as full spatial domain and 1 time step, with about 135MB chunk size.   This is actually great for visualization of maps at specific time steps or for calculations that involve the entire dataset. So kerchunking this data would be a nice first step. 

Let's check one out:

In [28]:
%%time
da = ds.ACCET.load()

CPU times: user 664 ms, sys: 164 ms, total: 828 ms
Wall time: 3.81 s


In [29]:
da.hvplot(x='x', y='y', rasterize=True, cmap='turbo', data_aspect=1)

:DynamicMap   [time]
   :Image   [x,y]   (ACCET)